In [1]:

!pip install --upgrade pip
!pip install transformers
!pip install datasets
!pip install rake_nltk
# !pip install --quiet bitsandbytes
!pip install --quiet accelerate

import pandas as pd  
import numpy as np 
# import tensorflow as tf
from accelerate import notebook_launcher
from datasets import Dataset,load_dataset, load_from_disk
from transformers import AutoTokenizer, AutoModelForSequenceClassification

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 22.4 MB/s eta 0:00:0000:010:01
  Attempting uninstall: pip
    Found existing installation: pip 22.3.1
    Uninstalling pip-22.3.1:
      Successfully uninstalled pip-22.3.1
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 20.6 MB/s eta 0:00:0000:010:01
  Attempting uninstall: nltk
    Found existing installation: nltk 3.2.4
    Uninstalling nltk-3.2.4:
      Successfully uninstalled nltk-3.2.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
preprocessing 0.1.13 requires nltk==3.2.4, but you have nltk 3.8.1 which is incompatible.


In [2]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Sun Apr 23 12:15:47 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.161.03   Driver Version: 470.161.03   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   37C    P8     8W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla T4            Off  | 00000000:00:05.0 Off |                    0 |
| N/A   

In [3]:
# tpu = tf.distribute.cluster_resolver.TPUClusterResolver.connect()

# # instantiate a distribution strategy
# tpu_strategy = tf.distribute.experimental.TPUStrategy(tpu)

In [4]:
data = pd.read_csv("/kaggle/input/dataset/dataset/train.csv")
data.head()

PRODUCT_ID                                              TITLE  \
0     1925202  ArtzFolio Tulip Flowers Blackout Curtain for D...   
1     2673191  Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2     2765088  PRIKNIK Horn Red Electric Air Horn Compressor ...   
3     1594019  ALISHAH Women's Cotton Ankle Length Leggings C...   
4      283658  The United Empire Loyalists: A Chronicle of th...   

                                       BULLET_POINTS  \
0  [LUXURIOUS & APPEALING: Beautiful custom-made ...   
1  [Harry Potter Hedwig Pyjamas (6-16 Yrs),100% c...   
2  [Loud Dual Tone Trumpet Horn, Compatible With ...   
3  [Made By 95%cotton and 5% Lycra which gives yo...   
4                                                NaN   

                                         DESCRIPTION  PRODUCT_TYPE_ID  \
0                                                NaN             1650   
1                                                NaN             2755   
2  Specifications: Color: Red, Material: Aluminiu...             7537   
3  AISHAH Women's Lycra Cotton Ankel Leggings. Br...             2996   
4                                                NaN             6112   

   PRODUCT_LENGTH  
0     2125.980000  
1      393.700000  
2      748.031495  
3      787.401574  
4      598.424000

In [5]:
data = data.dropna(axis = 0, subset = ["BULLET_POINTS"])

In [6]:
pip install -U scikit-learn

Note: you may need to restart the kernel to use updated packages.


In [7]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
data[['PRODUCT_LENGTH']] = scaler.fit_transform(data[['PRODUCT_LENGTH']])

In [8]:
data.head()

PRODUCT_ID                                              TITLE  \
0     1925202  ArtzFolio Tulip Flowers Blackout Curtain for D...   
1     2673191  Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2     2765088  PRIKNIK Horn Red Electric Air Horn Compressor ...   
3     1594019  ALISHAH Women's Cotton Ankle Length Leggings C...   
5     2152929  HINS Metal Bucket Shape Plant Pot for Indoor &...   

                                       BULLET_POINTS  \
0  [LUXURIOUS & APPEALING: Beautiful custom-made ...   
1  [Harry Potter Hedwig Pyjamas (6-16 Yrs),100% c...   
2  [Loud Dual Tone Trumpet Horn, Compatible With ...   
3  [Made By 95%cotton and 5% Lycra which gives yo...   
5  [Simple and elegant, great for displaying indo...   

                                         DESCRIPTION  PRODUCT_TYPE_ID  \
0                                                NaN             1650   
1                                                NaN             2755   
2  Specifications: Color: Red, Material: Aluminiu...             7537   
3  AISHAH Women's Lycra Cotton Ankel Leggings. Br...             2996   
5  HINS Brings you the most Elegant Looking Pot w...             5725   

   PRODUCT_LENGTH  
0       -0.002158  
1       -0.003174  
2       -0.002966  
3       -0.002943  
5       -0.002847

In [9]:
data = data.iloc[:800, [2,5 ]]

In [10]:
# import nltk
# nltk.download('stopwords')
# nltk.download('punkt')
from rake_nltk import Rake

rake_nltk_var = Rake()
keywords = []
for i in range(len(data)): 
    text = data.iloc[i, 0]
    rake_nltk_var.extract_keywords_from_text(text)
    keyword_extracted = rake_nltk_var.get_ranked_phrases()[:5]
    keyword_extracted = list(set(keyword_extracted))
    keyword_extracted = ', '.join(map(str, keyword_extracted))
    keywords.append(keyword_extracted)
data["BULLET_POINTS"] = keywords
data.head()

BULLET_POINTS  PRODUCT_LENGTH
0  2 room curtains eyelets, art digital printing ...       -0.002158
1  exclusive, 16 yrs ), 100, harry potter hedwig ...       -0.003174
2  professional installation required, electric a...       -0.002966
3  high quality steaching, elasticized waist band...       -0.002943
5  displaying indoor plants like succulent plants...       -0.002847

In [11]:
data.iloc[9, 0]

'single layer wall stainless steel water bottle, food grade steel, segovia bottle consists, special design along, adding hot water .]'

In [12]:
dataset = Dataset.from_pandas(data,preserve_index=False) 
dataset = dataset.rename_column("PRODUCT_LENGTH", "labels")
dataset = dataset.rename_column("BULLET_POINTS", "text")

In [13]:
print(dataset)

Dataset({
    features: ['text', 'labels'],
    num_rows: 800
})


In [14]:
dataset = dataset.train_test_split(test_size=0.3) 

In [15]:
selected_column = "text"

In [16]:
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-multilingual-cased")

In [17]:
def tokenize_function(dataset):
    return tokenizer(dataset[selected_column], padding="max_length", truncation=True)

tokenized_data = dataset.map(tokenize_function, batched=True)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [18]:

# !pip install git+https://github.com/huggingface/transformers.git
model = AutoModelForSequenceClassification.from_pretrained("distilbert-base-multilingual-cased", num_labels=1)

Some weights of the model checkpoint at distilbert-base-multilingual-cased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_transform.weight', 'vocab_projector.weight', 'vocab_projector.bias', 'vocab_layer_norm.weight', 'vocab_layer_norm.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'pre_classif

In [19]:
from datasets import load_metric
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error

def compute_metrics(eval_pred):
            predictions, labels = eval_pred
#     rmse = mean_squared_error(labels, predictions, squared=False)
            mape = mean_absolute_percentage_error(labels,predictions)
            return {"mape": mape}



In [20]:


from transformers import TrainingArguments, Trainer
def train_trainer_ddp():
    global trainer
    training_args = TrainingArguments(output_dir="test_trainer",
                                      logging_strategy="epoch",
                                      evaluation_strategy="epoch",
                                      per_device_train_batch_size=16,
                                      per_device_eval_batch_size=16,
                                      num_train_epochs=30,     
                                      greater_is_better = False,
                                      save_strategy="epoch",
                                      save_total_limit=2,
                                      metric_for_best_model="mape",
                                      load_best_model_at_end=True,
                                      weight_decay=0.01,
                                      fp16 = True
                                      )

    
        
    trainer = Trainer(
            model=model,
            args=training_args,
            train_dataset=tokenized_data["train"],
            eval_dataset=tokenized_data["test"],
            compute_metrics=compute_metrics,
            

        )
    trainer.train()
     
notebook_launcher(train_trainer_ddp, args=(), num_processes=2)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
Launching training on one GPU.


/opt/conda/lib/python3.7/site-packages/transformers/optimization.py:395: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

  ········································


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


/opt/conda/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


/opt/conda/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/opt/conda/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/opt/conda/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/opt/conda/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqu

In [21]:
model.save_pretrained("model")
tokenizer.save_pretrained("tokenizer")

('tokenizer/tokenizer_config.json',
 'tokenizer/special_tokens_map.json',
 'tokenizer/vocab.txt',
 'tokenizer/added_tokens.json',
 'tokenizer/tokenizer.json')

In [22]:
from transformers import AutoModelForTokenClassification
model = AutoModelForSequenceClassification.from_pretrained("model")
tokenizer = AutoTokenizer.from_pretrained("tokenizer")

In [23]:
def pipeline_prediction(text):
    df=pd.DataFrame({'text':[text]})
    dataset = Dataset.from_pandas(df,preserve_index=False) 
    tokenized_datasets = dataset.map(tokenize_function)
    raw_pred, _, _ = trainer.predict(tokenized_datasets) 
    return(raw_pred[0][0])

In [24]:
y_pred = [] 
for i in dataset["test"]["text"]: 
        y_pred.append(pipeline_prediction(i))
        
y_pred = scaler.inverse_transform([y_pred])
print((y_pred)) 
y_real = dataset["test"]["labels"]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

...

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

[[  1674.68213634   3598.18627381  -6006.32677777    975.52171444
    2575.46091247   -689.45566237   1125.10952564   3468.10991625
    2968.9418941     884.46826415   2419.36928339    461.72010207
    1131.61334352    702.36136356   -985.37937582    803.17054067
    1271.4454279    2429.12501021   1882.80430844   1274.69733684
     634.07127584   1560.86532348  -1395.11990215    -58.58532819
    2474.65173536   2515.3005971    -530.11212435   -217.9288662
   -2012.98260057   3975.40771074   1232.42252063   2486.03341664
     663.33845629    526.75828085   1268.19351896  -1544.70771335
    2364.08683143   4336.36960298   -126.87541591   2539.68991414
     100.75820983   2515.3005971    2204.74329341    169.04829755
    1619.39968438    780.4071781    3251.8579718    3277.87324331
    3357.54501232    559.27737024   2487.65937111   2699.03345215
    1580.37677711    308.88038193   2347.82728673   3030.72816394
    2123.44556994   4233.9344714    3933.13289454   1912.0714889
    2765.697

In [25]:

y_real = scaler.inverse_transform([y_real])
print(y_real)

[[1.18110236e+03 7.90000000e+02 5.90551180e+02 1.06000000e+03
  5.90550000e+02 2.95275590e+02 1.00000000e+02 1.96850000e+02
  2.00000000e+02 3.62204724e+03 7.20077300e+03 7.00000000e+02
  1.00000000e+03 4.18370000e+02 3.93700787e+02 6.69291338e+02
  5.90551180e+02 5.90551180e+02 1.65354331e+04 3.50000000e+02
  1.99200000e+03 1.18110236e+03 6.00000000e+02 3.54330708e+03
  3.93700787e+03 4.60000000e+03 4.50000000e+02 8.00000000e+02
  8.66141731e+02 2.36220472e+03 3.93700787e+01 4.00000000e+01
  7.48031495e+02 4.09448000e+02 6.29921259e+02 9.40000000e+02
  2.12598425e+03 9.05511810e+02 8.66141731e+02 1.08267716e+03
  3.25700000e+03 9.84251968e+02 1.30000000e+03 3.54330708e+02
  1.57480315e+02 1.18110236e+03 5.90000000e+02 1.11023622e+03
  1.96850393e+03 8.26771653e+02 1.80000000e+03 5.00000000e+02
  3.14960000e+01 5.00000000e+02 8.40000000e+03 9.84250000e+02
  2.75590551e+02 2.40000000e+03 1.96850393e+02 1.30000000e+03
  2.75590551e+02 2.40000000e+03 8.00000000e+02 4.72440944e+02
  8.2677

In [26]:
print(mean_absolute_percentage_error(y_real,y_pred))

6.198337292074525


In [27]:
test_data = pd.read_csv("/kaggle/input/dataset/dataset/test.csv")
test_data.set_index("PRODUCT_ID")
test_data.head()

PRODUCT_ID                                              TITLE  \
0      604373  Manuel d'Héliogravure Et de Photogravure En Re...   
1     1729783  DCGARING Microfiber Throw Blanket Warm Fuzzy P...   
2     1871949  I-Match Auto Parts Front License Plate Bracket...   
3     1107571  PinMart Gold Plated Excellence in Service 1 Ye...   
4      624253  Visual Mathematics, Illustrated by the TI-92 a...   

                                       BULLET_POINTS  \
0                                                NaN   
1  [QUALITY GUARANTEED: Luxury cozy plush polyest...   
2  [Front License Plate Bracket Made Of Plastic,D...   
3  [Available as a single item or bulk packed. Se...   
4                                                NaN   

                                         DESCRIPTION  PRODUCT_TYPE_ID  
0                                                NaN             6142  
1  <b>DCGARING Throw Blanket</b><br><br> <b>Size ...             1622  
2  Replacement for The Following Vehicles:2020 LE...             7540  
3  Our Excellence in Service Lapel Pins feature a...            12442  
4                                                NaN             6318

In [28]:
test_data = test_data.dropna(axis = 0, subset = ["BULLET_POINTS"])

In [29]:
test_data = test_data.set_index("PRODUCT_ID")

In [30]:
test_data.head()

TITLE  \
PRODUCT_ID                                                      
1729783     DCGARING Microfiber Throw Blanket Warm Fuzzy P...   
1871949     I-Match Auto Parts Front License Plate Bracket...   
1107571     PinMart Gold Plated Excellence in Service 1 Ye...   
2782548     Evershine Shoppee 10m Waxed Nylon Thread Cotto...   
1605901     Vasque Men's Velocity at Hiking Shoe, Dark Spr...   

                                                BULLET_POINTS  \
PRODUCT_ID                                                      
1729783     [QUALITY GUARANTEED: Luxury cozy plush polyest...   
1871949     [Front License Plate Bracket Made Of Plastic,D...   
1107571     [Available as a single item or bulk packed. Se...   
2782548     [Kindly Refer The Product Description Before B...   
1605901     [The velocity all-terrain is a streamlined hik...   

                                                  DESCRIPTION  PRODUCT_TYPE_ID  
PRODUCT_ID                                                                      
1729783     <b>DCGARING Throw Blanket</b><br><br> <b>Size ...             1622  
1871949     Replacement for The Following Vehicles:2020 LE...             7540  
1107571     Our Excellence in Service Lapel Pins feature a...            12442  
2782548     Description: Material: Nylon Length: about 10m...            11205  
1605901                                                   NaN             3234

In [31]:
test_data = test_data.iloc[:, 1]

In [32]:
test_data = test_data.to_frame(name = "text")


In [33]:
#test_data = test_data.reset_index(drop=True)
test_data.head()

text
PRODUCT_ID                                                   
1729783     [QUALITY GUARANTEED: Luxury cozy plush polyest...
1871949     [Front License Plate Bracket Made Of Plastic,D...
1107571     [Available as a single item or bulk packed. Se...
2782548     [Kindly Refer The Product Description Before B...
1605901     [The velocity all-terrain is a streamlined hik...

In [35]:
rake_nltk_var = Rake()
keywords = []
for index, row in test_data.iterrows(): 
    text = row["text"]
    rake_nltk_var.extract_keywords_from_text(text)
    keyword_extracted = rake_nltk_var.get_ranked_phrases()[:5]
    keyword_extracted = list(set(keyword_extracted))
    keyword_extracted = ', '.join(map(str, keyword_extracted))
    keywords.append(keyword_extracted)
test_data["text"] = keywords
test_data.head()

text
PRODUCT_ID                                                   
1729783     super soft cozy luxury bed blanket, elegance ....
1871949     hardware included, replaces oem part number 52...
1107571     individually poly bagged .], jewelry quality l...
2782548     diy bracelet, jewelry making .], handmade diy ...
1605901     footbed anatomical high rebound footbed, outso...

In [36]:
test_data.iloc[0,0]

'super soft cozy luxury bed blanket, elegance ., super soft, season choose ., satisfaction guaranteed, home decor ., blanket size, luxury cozy plush polyester throw blanket'

In [37]:
test_dataset = Dataset.from_pandas(test_data,preserve_index=True) 

In [38]:
print(test_dataset)

Dataset({
    features: ['text', 'PRODUCT_ID'],
    num_rows: 458814
})


In [ ]:
 import csv

file = open('submission4.csv', 'w', newline='') 
writer = csv.writer(file)
     
writer.writerow(["PRODUCT_ID", "PRODUCT_LENGTH"])
    

count = 0
     # predicted_val = [] 

chunk_count = 10000
chunk_val = 0
for i in test_dataset["text"]: 
        if chunk_val == chunk_count: 
            file.close()
            file = open('submission4.csv', 'a', newline='') 
            chunk_val = 0 
            writer = csv.writer(file)
        writer.writerow([test_dataset[count]["PRODUCT_ID"],scaler.inverse_transform([[pipeline_prediction(i)]])[0][0]])
  
        count +=1
        chunk_val +=1
file.close()


  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

...

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

  0%|          | 0/1 [00:00<?, ?ex/s]

In [ ]:
predicted_val = scaler.inverse_transform([predicted_val])
print(predicted_val)

In [ ]:
print(predicted_val)

In [ ]:
print(test_dataset[0]["PRODUCT_ID"])
print(count)
print(predicted_val[0][10000])

In [ ]:
predicted = predicted_val[0].tolist()
count = 10001
while count < len(test_dataset):
    predicted.append(None)
    count +=1
print(count)

In [ ]:
len(predicted)

In [ ]:
#ds = ds.add_column("new_column", new_column)
test_dataset = test_dataset.add_column("PRODUCT_LENGTH", predicted)

In [ ]:
 test_dataset.to_csv("submission1.csv", index = None)

In [ ]:
null_data = pd.read_csv("/kaggle/input/dataset/dataset/test.csv")
null_data.set_index("PRODUCT_ID")
null_data.head()